# Resolution with Zgoubidoo

https://github.com/ULB-Metronu/zgoubidoo/

In [ ]:
%load_ext autoreload
%autoreload 2
import zgoubidoo
from zgoubidoo.commands import *
from zgoubidoo import ureg as _

import copy
import numpy as _np
import pandas as _pd

# Beam energy

In [ ]:
kin = zgoubidoo.Kinematics(3 * _.MeV)
kin

In [ ]:
kin.brho.to('cm kG')

# Create the vertical FFA cell (FDF triplet structure)

In [ ]:
vFFA_cell = VFFA('vFFA_cell', 
                 IL=2,
                 N = 3, 
                 XL = 250*_.cm, 
                 XM = [65, 113, 145]*_.cm, 
                 L = [0.4, 0.24, 0.4]*_.m, 
                 B0 = [2.5, -0.2*2.5, 2.5]*_.kG, 
                 K = [1.28,1.28,1.28]*(_.m)**-1, 
                 GAP = [0.2, 0.2, 0.2]*_.m)

In [ ]:
vFFA_cell

## Make a single particle beam with explicit coordinates

In [ ]:
beam_for_tracks = Objet2('BUNCH', BORO=kin.brho)
dpp=1
beam_for_tracks.add(_np.array([[-30.0, 261.0, 0.0, 0.0, dpp]]))

## Make a quick sequence with just a single cell

In [ ]:
zi = zgoubidoo.Input(name='vFFA_ring', 
                     line=[
                         beam_for_tracks,
                         Marker("START"),
                         vFFA_cell,
                         ChangeRef("ROTATION", TRANSFORMATIONS=[('ZR', -36*_.degree)]),
                         Marker('E_Cell'),
                       ])
zi.IL = 2
zi.XPAS= 0.5 * _.cm

In [ ]:
zi

In [ ]:
zi.survey(with_reference_trajectory=True, reference_kinematics=kin);

## Run Zgoubi

In [ ]:
z = zgoubidoo.Zgoubi()
zr = z(zi).collect()

In [ ]:
zr.print()

In [ ]:
zr.tracks

## Prepare nice plots

In [ ]:
tracks_global = zr.tracks_global
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.plot_beamline(beamline=zi, opacity = 0.4)

artist.scatter(
    x=tracks_global['XG'], 
    y=tracks_global['YG'],
    marker={'color': 'blue', 'size': 2},
    mode='markers',
    )

artist.fig['layout']['yaxis']['range'] = [-0.4,0.3]
artist.render()


In [ ]:
# Tracks are collected from the .plt file and converted to the global (cartesian) reference system
tracks_global = zr.tracks_global

# Make a plotly plot
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.scatter(
    x=tracks_global['X'], 
    y=tracks_global['BZ'],
    marker={'color': 'blue', 'size': 4},
    mode='markers',
    name= 'BZ',
    showlegend = True
    )
artist.render()

# Closed orbit search

In [ ]:
fit = Fit2('CO_FIT',PENALTY=1e-12,
          ITERATIONS=9999,
     PARAMS= [
         Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.Y_, parameter_range=[-1000.0, 1000.0]),
         Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.T_, parameter_range=[-1000.0, 1000.0]),
         Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.Z_, parameter_range=[-1000.0, 1000.0]),
         Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.P_, parameter_range=[-1000.0, 1000.0]),
     ],
     CONSTRAINTS=[
         Fit2.DifferenceEqualityConstraint(
             line=zi,
             place='#End',
             variable=Fit2.FitCoordinates.Y,
         ),
         Fit2.DifferenceEqualityConstraint(
             line=zi,
             place='#End',
             variable=Fit2.FitCoordinates.T,
             value = 0.0
         ),
         Fit2.DifferenceEqualityConstraint(
             line=zi,
             place='#End',
             variable=Fit2.FitCoordinates.Z,
         ),
         Fit2.DifferenceEqualityConstraint(
             line=zi,
             place='#End',
             variable=Fit2.FitCoordinates.P,
             value = 0.0
         ),
     ],   
)

fit

In [ ]:
zi += fit
zr = zgoubidoo.Zgoubi()(zi).collect()
zr.print()

In [ ]:
fit.results[0][1].results

In [ ]:
closed_orbit = []
y0 = fit.results[0][1].results.at[1, 'final']
t0 = fit.results[0][1].results.at[2, 'final']
z0 = fit.results[0][1].results.at[3, 'final']
p0 = fit.results[0][1].results.at[4, 'final']
closed_orbit.append([y0.magnitude, t0.magnitude, z0.magnitude, p0.magnitude, dpp])
closed_orbit

In [ ]:
# Track closed orbit
zi.remove('CO_FIT')
beam_for_tracks = Objet2('BUNCH', BORO=kin.brho)
beam_for_tracks.add(_np.array(closed_orbit))

zi.replace('BUNCH', beam_for_tracks)
zi.survey(with_reference_trajectory=True, reference_kinematics=kin, reference_closed_orbit=_np.array(closed_orbit))

z.cleanup()
zr = z(zi).collect()
co_tracks = zr.tracks_global

In [ ]:
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.fig['layout']['xaxis']['title'] = 'X (m)'
artist.fig['layout']['yaxis']['title'] = 'Y (m)'
artist.fig['layout']['yaxis']['scaleanchor'] = 'x'
artist.fig['layout']['yaxis']['scaleratio'] = 1

artist.plot_beamline(beamline=zi, opacity=0.8)
artist.scatter(
        x=co_tracks['XG'],
        y=co_tracks['YG'],
        marker={'color': 'black', 'symbol': 303, 'size': .3},
        line={'width': 2, },
        mode='markers',
    )
artist.render()

In [ ]:
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.fig['layout']['xaxis']['title'] = 'X (m)'
artist.fig['layout']['yaxis']['title'] = 'Z (m)'

artist.scatter(
        x=co_tracks['XG'],
        y=co_tracks['ZG'],
        marker={'color': 'black', 'symbol': 303, 'size': .3},
        line={'width': 2, },
        mode='markers',
    )
artist.render()

In [ ]:
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.fig['layout']['xaxis']['title'] = 'S (m)'
artist.fig['layout']['yaxis']['title'] = 'B (kGauss)'

artist.scatter(
        x=co_tracks['S'],
        y=co_tracks['BX'],
        marker={'color': 'black', 'symbol': 303, 'size': 2},
        name='BX',
        line={'width': 2, },
        mode='markers',
    )

artist.scatter(
        x=co_tracks['S'],
        y=co_tracks['BZ'],
        marker={'color': 'red', 'symbol': 303, 'size': 2},
        name='BZ',
        line={'width': 2, },
        mode='markers',
    )

artist.scatter(
        x=co_tracks['S'],
        y=co_tracks['BY'],
        marker={'color': 'blue', 'symbol': 303, 'size': 2},
        name='BY',
        line={'width': 2, },
        mode='markers',
    )

artist.render()

## Find the closed orbits for different energies

In [ ]:
beam_for_tracks = Objet2('BUNCH', BORO=kin.brho)
dpp=1
beam_for_tracks.add(_np.array([[-30.0, 261.0, 0.0, 0.0, dpp]]))
zi = zgoubidoo.Input(name='vFFA_ring', 
                     line=[
                         beam_for_tracks,
                         Marker("START"),
                         vFFA_cell,
                         ChangeRef("ROTATION", TRANSFORMATIONS=[('ZR', -36*_.degree)]),
                         Marker('E_Cell'),
                       ])
zi.IL = 2
zi.XPAS= 0.4 * _.cm
zi.survey(with_reference_trajectory=True, reference_kinematics=kin);
[y0, t0, z0, p0] = [-30.0*_.cm, 261.0*_.mrad, 0.0*_.cm, 0.0*_.mrad]

In [ ]:
orbits = []
dpps= [1.0, 1.25, 1.5, 1.75, 2.0, 2.25]
for i, dpp in enumerate(dpps):
    zi.remove('CO_FIT')
    param = [
        Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.Y_, parameter_range=[-1000.0, 1000.0]),
        Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.T_, parameter_range=[-1000.0, 1000.0]),
        Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.Z_, parameter_range=[-1000.0, 1000.0]),
        Fit2.Parameter(line=zi, place='BUNCH', parameter=Objet2.P_, parameter_range=[-1000.0, 1000.0]),
    ]

    fit_i = Fit2('CO_FIT',PENALTY=1e-12,
              ITERATIONS=9999,
         PARAMS= param,
         CONSTRAINTS=[
             Fit2.DifferenceEqualityConstraint(
                 line=zi,
                 place='#End',
                 variable=Fit2.FitCoordinates.Y,
             ),
             Fit2.DifferenceEqualityConstraint(
                 line=zi,
                 place='#End',
                 variable=Fit2.FitCoordinates.T,
                 value = 0.0
             ),
             Fit2.DifferenceEqualityConstraint(
                 line=zi,
                 place='#End',
                 variable=Fit2.FitCoordinates.Z,
             ),
             Fit2.DifferenceEqualityConstraint(
                 line=zi,
                 place='#End',
                 variable=Fit2.FitCoordinates.P,
                 value = 0.0
             ),
         ],   
    )

    ref_beam = Objet2('BUNCH', BORO=kin.brho)
    ref_beam.add(_np.array([
        [y0.magnitude, t0.magnitude, z0.magnitude, p0.magnitude, dpp]
    ]))
    zi.replace('BUNCH', ref_beam)    
    zi += fit_i
    zr = zgoubidoo.Zgoubi()(zi).collect()
    y0 = fit_i.results[0][1].results.at[1, 'final']
    t0 = fit_i.results[0][1].results.at[2, 'final']
    z0 = fit_i.results[0][1].results.at[3, 'final']
    p0 = fit_i.results[0][1].results.at[4, 'final']
    orbits.append([y0.magnitude, t0.magnitude, z0.magnitude, p0.magnitude, dpp])
    print(f"Closed orbit for dpp = {dpp}: y={y0.magnitude}, t={t0.magnitude}, z={z0.magnitude}, p={p0.magnitude}")

### Plot the closed orbits and magnetic field

In [ ]:
ref_beam = Objet2('BUNCH', BORO=kin.brho)
ref_beam.add(_np.array(orbits))
zi.remove('CO_FIT')
zi.replace('BUNCH', ref_beam)
zr = zgoubidoo.Zgoubi()(zi).collect()
tracks_global = zr.tracks_global

In [ ]:
dpps= [1.0, 1.25, 1.5, 1.75, 2.0, 2.25]
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.fig['layout']['xaxis']['title'] = 'S (m)'
artist.fig['layout']['yaxis']['title'] = 'Z (m)'

z0_unique = tracks_global.Zo.unique()
for z in z0_unique:
    name_ = str(_np.round(zgoubidoo.Kinematics(dpps.pop(0)*kin.momentum).ekin,1).magnitude)+' MeV'
    artist.scatter(
        x=tracks_global.query(f"Zo== {z}")['S'], 
        y=tracks_global.query(f"Zo== {z}")['ZG'],
        marker={'size': 2},
        mode='markers',
        name = name_
        )
artist.render()

In [ ]:
names = ['BZ', 'BY', 'BX']
for i in [0,1,2]:
    dpps= [1.0, 1.25, 1.5, 1.75, 2.0, 2.25]
    artist = zgoubidoo.vis.ZgoubidooPlotlyArtist(
    )
    artist.fig['layout']['xaxis']['title'] = 'S (m)'
    artist.fig['layout']['yaxis']['title'] = names[i]+'(kG)'

    z0_unique = tracks_global.Zo.unique()
    for z in z0_unique:
        name_ = str(_np.round(zgoubidoo.Kinematics(dpps.pop(0)*kin.momentum).ekin,1).magnitude)+' MeV'
        artist.scatter(
            x=tracks_global.query(f"Zo== {z}")['S'], 
            y=tracks_global.query(f"Zo== {z}")[names[i]],
            marker={'size': 2},
            mode='markers+ lines',
            name = name_
            )
    artist.render()

### Track in the full ring

In [ ]:
ref_beam = Objet2('BUNCH', BORO=kin.brho)
ref_beam.add(_np.array(orbits))
rot = ChangeRef("ROTATION", TRANSFORMATIONS=[('ZR', -36*_.degree)])
zi = zgoubidoo.Input(name='vFFA_ring', line=
               [
                   ref_beam,
                   vFFA_cell,
                   rot,
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
                   copy.copy(vFFA_cell),
                   copy.copy(rot),
               ])
zi.XPAS = 1*_.cm 
zi.survey(with_reference_trajectory=True, reference_kinematics=kin);

In [ ]:
zr = zgoubidoo.Zgoubi()(zi).collect()

In [ ]:
tracks_global = zr.tracks_global

In [ ]:
dpps= [1.0, 1.25, 1.5, 1.75, 2.0, 2.25]
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist(
)
artist.fig['layout']['yaxis']['title'] = 'Y (m)'
artist.fig['layout']['xaxis']['title'] = 'X (m)'

artist.plot_beamline(beamline=zi)
z0_unique = tracks_global.Zo.unique()
for z in z0_unique:
    name_ = str(_np.round(zgoubidoo.Kinematics(dpps.pop(0)*kin.momentum).ekin,1).magnitude)+' MeV'    
    artist.scatter(
        x=tracks_global.query(f"Zo== {z}")['XG'], 
        y=tracks_global.query(f"Zo== {z}")['YG'],
        marker={'size': 3},
        name=name_,
        mode='markers',
        )
artist.render()

# Let's compute the step-by-step transfer matrix and tune

In [ ]:
zi = zgoubidoo.Input(name='vFFA_ring', 
                     line=[
                         beam_for_tracks,
                         Marker("START"),
                         vFFA_cell,
                         ChangeRef("ROTATION", TRANSFORMATIONS=[('ZR', -36*_.degree)]),
                         #Matrix('matrix'),
                         Marker('E_Cell'),
                       ])
orbits = _np.array(orbits)

Ms=[]
for i, o in enumerate(orbits):
    print(_np.array([o]))
    twiss_beam = BeamTwiss('BUNCH', kinematics=kin, 
                           YR=[orbits[i, 0]], TR=[orbits[i, 1]], 
                           ZR=[orbits[i, 2]], PR=[orbits[i, 3]], 
                           DR=[orbits[i, 4]])
    zi.replace('BUNCH', twiss_beam)
    zi.survey(with_reference_trajectory=True, reference_kinematics=kin, reference_closed_orbit=_np.array([o]))
    zr = zgoubidoo.Zgoubi()(zi).collect()

    twiss_tracks = zr.tracks_frenet
    M = zgoubidoo.twiss.compute_transfer_matrix(
        beamline=zi, 
        tracks=twiss_tracks
    )
    #M = zr.matrix

    M_final = _np.array(M[['R11', 'R12', 'R13', 'R14', 'R15', 'R21', 'R22', 'R23', 'R24',
              'R25', 'R31', 'R32', 'R33', 'R34', 'R35', 'R41', 'R42', 'R43', 'R44',
              'R45', 'R51', 'R52', 'R53', 'R54', 'R55']].iloc[-1, :]).reshape(5, 5)[:4, :4]
    Ms.append(M_final)
    

In [ ]:
Ms[0]

In [ ]:
def tunes(M):
    eigvals, eigvec = _np.linalg.eig(M)
    tune1 = (_np.arctan(_np.imag(eigvals[0])/_np.real(eigvals[0]))/(2*_np.pi))
    tune2 = (_np.arctan(_np.imag(eigvals[2])/_np.real(eigvals[2]))/(2*_np.pi))
    return [tune1, tune2]

dpps = orbits[:, -1]
e_kin = [_np.round(zgoubidoo.Kinematics(kin.brho * dpp).ekin.m_as("MeV"),2) for dpp in dpps]
tunes_1 = [tunes(M)[0] for M in Ms]
tunes_2 = [tunes(M)[1] for M in Ms]

In [ ]:
artist = zgoubidoo.vis.ZgoubidooPlotlyArtist()
artist.fig['layout']['xaxis']['title'] = 'Energy (MeV)'
artist.fig['layout']['yaxis']['title'] = 'Cell eigentunes'

artist.scatter(
    x=e_kin, 
    y=tunes_1,
    marker={'color': 'blue', 'size': 6},
    name='Q1',
    mode='markers+ lines',
    )

artist.scatter(
    x=e_kin, 
    y=tunes_2,
    marker={'color': 'red', 'size': 6},
    name='Q2',
    mode='markers+ lines',
    )

artist.render()
